# HW2 DATASCI W261: Machine Learning at Scale 

* **Name:**  Megan Jasek
* **Email:**  meganjasek@ischool.berkeley.edu
* **Class Name:**  W261-2
* **Week Number:**  3
* **Date:**  5/31/16

**HW3.0.**
How do you merge  two sorted  lists/arrays of records of the form [key, value]? Where is this  used in Hadoop MapReduce? [Hint within the shuffle]
What is  a combiner function in the context of Hadoop? 
Give an example where it can be used and justify why it should be used in the context of this problem.
What is the Hadoop shuffle?

**HW3.1** Consumer complaints dataset: Use Counters to do EDA (exploratory data analysis and to monitor progress.  
Now, let’s use Hadoop Counters to identify the number of complaints pertaining to debt collection, mortgage and other categories (all other categories get lumped into this one) in the consumer complaints dataset. Basically produce the distribution of the Product column in this dataset using counters (limited to 3 counters here).

Hadoop offers Job Tracker, an UI tool to determine the status and statistics of all jobs. Using the job tracker UI, developers can view the Counters that have been created. Screenshot your  job tracker UI as your job completes and include it here. Make sure that your user defined counters are visible. 

In [29]:
# Read the Consumer_Complaints.csv input file into HDFS
#!/usr/local/hadoop/bin/hdfs dfs -copyFromLocal Consumer_Complaints.csv /user/hadoop
#!/usr/local/hadoop/bin/hdfs dfs -copyFromLocal Consumer_Complaints_small.csv /user/hadoop
!/usr/local/hadoop/bin/hdfs dfs -ls /user/hadoop

16/05/27 00:04:22 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Found 18 items
-rw-r--r--   3 hadoop supergroup   50906486 2016-05-26 23:08 /user/hadoop/Consumer_Complaints.csv
-rw-r--r--   3 hadoop supergroup      16478 2016-05-27 00:04 /user/hadoop/Consumer_Complaints_small.csv
-rw-r--r--   3 hadoop supergroup     203981 2016-05-21 14:24 /user/hadoop/enronemail_1h.txt
drwxr-xr-x   - hadoop supergroup          0 2016-05-26 12:20 /user/hadoop/outputHW2-0-1
drwxr-xr-x   - hadoop supergroup          0 2016-05-21 14:06 /user/hadoop/outputHW2-1
drwxr-xr-x   - hadoop supergroup          0 2016-05-25 23:36 /user/hadoop/outputHW2-2
drwxr-xr-x   - hadoop supergroup          0 2016-05-26 12:57 /user/hadoop/outputHW2-2-1
drwxr-xr-x   - hadoop supergroup          0 2016-05-21 22:39 /user/hadoop/outputHW2-3
drwxr-xr-x   - hadoop supergroup          0 2016-05-25 11:35 /user/hadoop/outputHW2-3a
drwxr-xr-x   - hadoop 

In [56]:
%%writefile mapper.py
#!/usr/bin/env python
## mapper.py
## Author: Megan Jasek
## Description: mapper code for HW3.1

import sys

sys.stderr.write("reporter:counter:Mapper Counters,Calls,1\n")
sys.stderr.write("reporter:status:processing my message...how are you\n")

# input comes from STDIN (standard input)
for line in sys.stdin:
    items = line.split(',')
    product = items[1].lower()
    if product == "product":
        continue
    elif product == "debt collection":
        sys.stderr.write("reporter:counter:EDA Counters,Debt,1\n")
    elif product == "mortgage":
        sys.stderr.write("reporter:counter:EDA Counters,Mortgage,1\n")
    else:
        sys.stderr.write("reporter:counter:EDA Counters,Others,1\n")        
    print('%s\t%d' % (product, 1))

Overwriting mapper.py


In [48]:
%%writefile reducer.py
#!/usr/bin/env python
## reducer.py
## Author: Megan Jasek
## Description: reducer code for HW3.1

import sys

sys.stderr.write("reporter:counter:Reducer Counters,Calls,1\n")

cur_key = None
cur_count = 0
for line in sys.stdin:
    items = line.split('\t')
    key = items[0]
    value = items[1]
    if key == cur_key:
        cur_count += int(value)
    else:
        if cur_key:
            print '%s\t%s' % (cur_key, cur_count)
        cur_key = key
        cur_count = int(value)

print '%s\t%s' % (cur_key, cur_count)

Overwriting reducer.py


In [57]:
# Remove output from previous runs of this command
!/usr/local/hadoop/bin/hdfs dfs -rm /user/hadoop/outputHW3-1/*
!/usr/local/hadoop/bin/hdfs dfs -rmdir /user/hadoop/outputHW3-1
# Run a Hadoop streaming job.  The input file 'Consumer_Complaints.csv' is passed as input.
!/usr/local/hadoop/bin/hadoop jar /usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-2.7.1.jar \
-files mapper.py,reducer.py -mapper mapper.py -reducer reducer.py \
-input /user/hadoop/Consumer_Complaints.csv -output /user/hadoop/outputHW3-1

16/05/27 00:19:04 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
16/05/27 00:19:05 INFO fs.TrashPolicyDefault: Namenode trash configuration: Deletion interval = 0 minutes, Emptier interval = 0 minutes.
Deleted /user/hadoop/outputHW3-1/_SUCCESS
16/05/27 00:19:05 INFO fs.TrashPolicyDefault: Namenode trash configuration: Deletion interval = 0 minutes, Emptier interval = 0 minutes.
Deleted /user/hadoop/outputHW3-1/part-00000
16/05/27 00:19:06 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
16/05/27 00:19:07 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
packageJobJar: [/tmp/hadoop-unjar1206062182772017196/] [] /tmp/streamjob6527218966918518898.jar tmpDir=null
16/05/27 00:19:08 INFO client.RMProxy: Connecting to ResourceManager at master/50.97.205

In [58]:
# Print out what files were created from the MapReduce job
!/usr/local/hadoop/bin/hdfs dfs -ls /user/hadoop/outputHW3-1
# Print the output file
!/usr/local/hadoop/bin/hdfs dfs -cat /user/hadoop/outputHW3-1/part-00000

16/05/27 00:19:45 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Found 2 items
-rw-r--r--   3 hadoop supergroup          0 2016-05-27 00:19 /user/hadoop/outputHW3-1/_SUCCESS
-rw-r--r--   3 hadoop supergroup        184 2016-05-27 00:19 /user/hadoop/outputHW3-1/part-00000
16/05/27 00:19:47 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
bank account or service	38073
consumer loan	9387
credit card	41563
credit reporting	41214
debt collection	44372
money transfers	1540
mortgage	125752
payday loan	1579
student loan	9432


In [ ]:
# input comes from STDIN (standard input)
filename = "Consumer_Complaints.csv"
with open(filename, 'r') as f:
    for line in f.readlines():
        items = line.split(',')
        product = items[1]
        if product == "Debt collection":
            #sys.stderr.write("reporter:counter:EDA Counters,Debt,1\n")
            pass
        elif product == "Mortgage":
            #sys.stderr.write("reporter:counter:EDA Counters,Mortgage,1\n")
            pass
        else:
            #sys.stderr.write("reporter:counter:EDA Counters,Others,1\n")
            pass
        print '%s\t%d' % (product, 1)

Product	1
Debt collection	1
Debt collection	1
Bank account or service	1
Debt collection	1
Credit reporting	1
Debt collection	1
Consumer loan	1
Debt collection	1
Consumer loan	1
Debt collection	1
Credit reporting	1
Credit reporting	1
Debt collection	1
Mortgage	1
Credit reporting	1
Credit reporting	1
Debt collection	1
Debt collection	1
Debt collection	1
Credit reporting	1
Mortgage	1
Debt collection	1
Bank account or service	1
Credit reporting	1
Debt collection	1
Credit reporting	1
Consumer loan	1
Credit reporting	1
Bank account or service	1
Debt collection	1
Bank account or service	1
Mortgage	1
Credit reporting	1
Credit reporting	1
Bank account or service	1
Debt collection	1
Debt collection	1
Debt collection	1
Credit reporting	1
Debt collection	1
Debt collection	1
Debt collection	1
Credit card	1
Credit reporting	1
Credit reporting	1
Credit reporting	1
Credit reporting	1
Credit reporting	1
Debt collection	1
Credit reporting	1
Credit reporting	1
Debt collection	1
Debt collection	1
Credit c